# RAW DATA


In [0]:
# Read the Delta table from the specified storage location
delta_table_path = "/mnt/prod_rawdata/hackathon"
review_df = spark.read.format("delta").load(delta_table_path)

# Display the DataFrame
display(review_df)

# INITIAL TRANSFORMATIONS AND LINKAGE 

In [0]:
%sql
SELECT * FROM default.trustpilot_review_data

REVIEW_ID COUNTRY_CODE STARS TITLE TEXT TRANSLATION EXPERIENCED_AT LAST_MSISDN_STATUS LAST_CUSTOMER_TYPE_SR_KEY LAST_USAGE_DATE SUBSCRIBER_SR_KEY 653eb0e29b2bf4b22f31e27f NLD 5 Fijne service Fijne service Great service. 2023-10-29 Active 1 2024-11-27T23:59:59Z 129154413 6533ef0945e1c6dcb4b0c787 NLD 5 heldere informatie en makkelijk te… heldere informatie en makkelijk te bestellen Clear information and easy to order. 2023-10-21 Active 2 2024-11-14T07:43:37Z 132288948 650b18270438cc88614868c0 NLD 5 gratis sim kaart gratis sim kaart Free SIM card. 2023-09-20 Expired 5 2024-06-01T23:59:59Z 131020322 6523fef3d4ad5b62b8bf962a NLD 5 Kan niet eenvoudiger Snel, eenvoudig en goedkoop en netwerk KPN Fast, simple, and cheap on KPN network. 2023-10-09 Expired 2 2024-02-12T21:39:40Z 131824786 65cce885fa1a1f224f3ed286 NLD 5 Good offers and good customer service Good offers and good customer service Good offers and good customer service 2024-02-14 Expired 5 2023-07-16T23:59:59Z 129865177 65e968afa3b2ac16ca035758 NLD 3 Was beetje onduidelijk dat er nieuwe… Was beetje onduidelijk dat er nieuwe nummer bij zat It was a bit unclear that there was a new song included. 2024-03-07 Dormant -1 null 137159580 6575b2e4a07a9833d848775f NLD 5 Snelle service Snelle service, zeer redelijke prijzen en aantrekkelijke aanbiedingen Fast service, very reasonable prices, and attractive offers. 2023-12-09 Active 2 2024-10-29T16:12:07Z 139942838 6593fbddd0b482d4804ef543 NLD 5 De overstap is keurig geregeld. De overstap is keurig geregeld. The switch has been arranged neatly. 2024-01-02 Active 1 2024-11-27T23:59:59Z 134251166 65e84eb658b9f3eb379a7141 NLD 1 Een Ongelooflijk Teleurstellende Ervaring met Lebara's Financiële Afdeling Als trouwe klant van Lebara ben ik diep teleurgesteld en gefrustreerd over de absoluut verschrikkelijke service die ik heb ontvangen van hun financiële afdeling. Het is ongelooflijk dat een bedrijf van dit formaat zulke fundamentele aspecten van klantenservice niet kan vervullen, zoals het verstrekken van eenvoudige facturen na herhaalde beloften.

Na meerdere keren contact te hebben opgenomen met Lebara's financiële afdeling om een factuur te verkrijgen voor mijn betalingen, ben ik keer op keer teleurgesteld. Elke keer dat ik bel, wordt mij verzekerd dat de factuur "spoedig" zal worden verzonden. Maar, zoals te verwachten was, komt er nooit iets. Dit gebrek aan follow-up en respect voor hun klanten is schandalig en onaanvaardbaar.

Later kreeg ik zelfs een onzinnig advies te horen: namelijk om een screenshot te maken van mijn betaling en deze screenshot te gebruiken voor mijn belastingadministratie. Dit advies werd mij gegeven terwijl ik een zakelijk account heb.

Een screenshot van een betaling is geen geldig vervanging voor een factuur, zoals je al hebt opgemerkt. Facturen zijn essentieel voor de administratie van bedrijven en worden gebruikt voor belastingdoeleinden, boekhouding en wettelijke naleving.

In werkelijkheid is het voor zakelijke transacties essentieel om correcte en gedetailleerde facturen te hebben die voldoen aan de wettelijke vereisten van de belastingdienst. Een screenshot van een betaling is geen geldige vervanging voor een factuur, omdat het niet alle benodigde informatie bevat die nodig is voor belastingdoeleinden, zoals factuurdatum, factuurnummer, btw-identificatienummer, etc.

Als je een zakelijke overeenkomst hebt met Lebara, hebben zij de verplichting om correcte facturen te verstrekken voor de geleverde diensten. 

De frustratie die dit veroorzaakt is onbeschrijfelijk. Het is niet alleen een kwestie van het ontvangen van een factuur, maar ook van het gevoel dat mijn verzoek om een eenvoudige administratieve taak te voltooien totaal genegeerd wordt. Het lijkt erop dat Lebara's financiële afdeling totaal onbekwaam is om zelfs de meest basale taken uit te voeren.

Het is duidelijk dat Lebara niet geeft om de tevredenheid van haar klanten, noch om het nakomen van haar beloften. Als dit de manier is waarop ze hun fin

# SENTIMENTAL ANALYSIS

## Hugging Face PreTrained model

In [0]:
# Import hugging face libraries and pandas
from transformers import pipeline
import pandas as pd
#Convert the DataFrame to a pandas DataFrame
review_df = spark.sql("SELECT * FROM default.trustpilot_review_data where length(TRANSLATION)<=512").toPandas()

## Feed data to analyzer 


In [0]:
def analyze_sentiment(review):
    result = sentiment_analyzer(review)[0]
    return pd.Series([result['label'], result['score']])


review_df[['sentiment', 'score']] = review_df['TRANSLATION'].apply(analyze_sentiment)
review_spark_df = spark.createDataFrame(review_df)


## Save data to table

In [0]:
 review_spark_df.write.mode('overwrite').saveAsTable('default.trustpilot_review_data_sentiment')

## REFINE SENTIMENTS TO ALIGN WITH LEBARA


### Normalize Sentiment

In [0]:
%sql
update default.trustpilot_review_data_sentiment 
set normalized_sentiment = 'NEGATIVE'
where sentiment = 'POSITIVE'
and stars in(2 ,1 )
and TRANSLATION = 'n/a'

In [0]:
%sql 
update default.trustpilot_review_data_sentiment 
set normalized_sentiment = 'NEUTRAL'
where 1 = 1 --sentiment = 'POSITIVE'
and stars = 3 
and TRANSLATION = 'n/a'

In [0]:
%sql 
-- negative star review preceeds the positive sentiment in general 
update default.trustpilot_review_data_sentiment 
set normalized_sentiment = 'NEGATIVE'
where sentiment = 'POSITIVE'
and stars = 1 

In [0]:
%sql 
-- for leabar cheap is good 
update default.trustpilot_review_data_sentiment 
set normalized_sentiment = 'POSITIVE'
where sentiment = 'NEGATIVE'
and stars in ( 4 , 5)
and translation like '%cheap%'

In [0]:
%sql 
update default.trustpilot_review_data_sentiment 
set normalized_sentiment = 'POSITIVE'
where sentiment = 'NEGATIVE'
and stars in ( 4 , 5)
and translation like '%good%'
and NORMALIZED_SENTIMENT is null 

In [0]:
%sql 
update default.trustpilot_review_data_sentiment 
set normalized_sentiment = 'POSITIVE'
where sentiment = 'NEGATIVE'
and stars in ( 4 , 5)
and translation like '%good%'
and NORMALIZED_SENTIMENT is null 

In [0]:

%sql 
update default.trustpilot_review_data_sentiment 
set normalized_sentiment = 'NEGATIVE'
where sentiment = 'POSITIVE'
and stars in(2 ,1 )
and TRANSLATION = 'n/a'

#DATA ENRICHMENT

-  - Add Churn Score 
-  - Average Customer Value 
-  - Pre paid vs Post paid 
-  - Tenure 
-  - Customer Type 

In [0]:
review_df = spark.sql("select * from default.trustpilot_review_data_sentiment")
review_df = review_df.join(churn_df_final, 'SUBSCRIBER_SR_KEY', 'left').select(review_df["*"], churn_df_final["PREDICTION_SCORE"].alias('CHURN_PREDICTION_SCORE'))
review_df = review_df.withColumn('PREDICTION_SCORE', F.coalesce(F.col('CHURN_PREDICTION_SCORE'), F.col('PREDICTION_SCORE')))
review_df = review_df.drop('CHURN_PREDICTION_SCORE')
review_df = review_df.withColumn("CUSTOMER_TYPE",F.when(F.col('LAST_CUSTOMER_TYPE_SR_KEY')==1, F.lit("POSTPAID")).when(F.col('LAST_CUSTOMER_TYPE_SR_KEY').isin([2,4,5]), F.lit("PREPAID")).otherwise(F.lit("UNKNOWN")))
review_df = review_df.withColumn("NORMALIZED_SENTIMENT", F.lit(None))
review_df.write.mode('overwrite').saveAsTable('default.trustpilot_review_data_sentiment')

# KEYWORD EXTRACTION


In [0]:
# install libraries
%pip install keybert

### Function to extract keywords

In [0]:
from keybert import KeyBERT
from sentence_transformers import SentenceTransformer

sentence_model = SentenceTransformer("all-MiniLM-L6-v2")
kw_model = KeyBERT(model=sentence_model)

In [0]:
def extract_keyword(review):
    keywords = kw_model.extract_keywords(review, keyphrase_ngram_range=(3, 3), stop_words='english',
                              use_mmr=True, diversity=0.2)
    
    try:
      val = pd.Series([list(keywords[0])[0], list(keywords[1])[0], list(keywords[2])[0], list(keywords[3])[0], list(keywords[4])[0]])
      return val
    except:
      return pd.Series([None, None, None, None, None])

In [0]:
#Convert table  to pandas dataframe
review_df = spark.sql('select REVIEW_ID, TRANSLATION from trustpilot_review_data_sentiment').toPandas()

In [0]:
review_df[['KEYWORD_1', 'KEYWORD_2', 'KEYWORD_3', 'KEYWORD_4', 'KEYWORD_5']] = review_df['TRANSLATION'].apply(extract_keyword)
review_spark_df = spark.createDataFrame(review_df)
review_spark_df.write.mode('overwrite').saveAsTable('default.trustpilot_review_data_with_keyword')

In [0]:
from pyspark.sql import functions as F
keyword_df = spark.table('trustpilot_review_data_with_keyword')
keyword_df = keyword_df.filter(F.col('KEYWORD_1').isNotNull())
review_df = spark.table('trustpilot_review_data_sentiment')
keyword_df = keyword_df.selectExpr("REVIEW_ID", "TRANSLATION","stack(5, 'KEYWORD_1', KEYWORD_1, 'KEYWORD_2', KEYWORD_2, 'KEYWORD_3', KEYWORD_3, 'KEYWORD_4', KEYWORD_4, 'KEYWORD_5', KEYWORD_5) as (KEYWORD,value)")
unpivoted_keyword_df = keyword_df.drop('KEYWORD').withColumnRenamed('value','KEYWORD')
unpivoted_keyword_final_df = unpivoted_keyword_df.join(review_df, 'REVIEW_ID').select(unpivoted_keyword_df['REVIEW_ID'], review_df['COUNTRY_CODE'], review_df["STARS"],  unpivoted_keyword_df['KEYWORD'], review_df['EXPERIENCED_AT'])
unpivoted_keyword_final_df.write.mode('overwrite').saveAsTable('default.trustpilot_review_data_stars_with_keyword')

## Final Keyword extracted data

In [0]:
%sql
select * from trustpilot_review_data_stars_with_keyword--where STARS=1 group by KEYWORD

REVIEW_ID COUNTRY_CODE STARS KEYWORD EXPERIENCED_AT 65097fb5c5322dc533d19ed0 GBR 5 patient diligent polite 2023-09-19 65097fb5c5322dc533d19ed0 GBR 5 great customer service 2023-09-19 65097fb5c5322dc533d19ed0 GBR 5 buttons help straight 2023-09-19 65097fb5c5322dc533d19ed0 GBR 5 able right buttons 2023-09-19 65097fb5c5322dc533d19ed0 GBR 5 gauri extremely knowledgeable 2023-09-19 65098723c320e722d1536567 GBR 5 problem fixed helped 2023-09-19 65098723c320e722d1536567 GBR 5 helped sort patiently 2023-09-19 65098723c320e722d1536567 GBR 5 solving text messages 2023-09-19 65098723c320e722d1536567 GBR 5 text messages problem 2023-09-19 65098723c320e722d1536567 GBR 5 aniket helpful patient 2023-09-19 6509959f2d24a89f61fad441 GBR 5 work properly contacted 2023-09-19 6509959f2d24a89f61fad441 GBR 5 service chat certain 2023-09-19 6509959f2d24a89f61fad441 GBR 5 texts sending arriving 2023-09-19 6509959f2d24a89f61fad441 GBR 5 problem texts sending 2023-09-19 6509959f2d24a89f61fad441 GBR 5 just changed lebara 2023-09-19 6509ada57a049575df18604a DEU 5 lot completely satisfied 2023-09-19 6509ada57a049575df18604a DEU 5 idrissi helped lot 2023-09-19 6509ada57a049575df18604a DEU 5 friendly employee mr 2023-09-19 6509ada57a049575df18604a DEU 5 mr idrissi helped 2023-09-19 6509ada57a049575df18604a DEU 5 employee mr idrissi 2023-09-19 6509ff93487467c5384c1dcc DNK 2 card new subscription 2023-09-19 6509ff93487467c5384c1dcc DNK 2 website kept failing 2023-09-19 6509ff93487467c5384c1dcc DNK 2 order new sim 2023-09-19 6509ff93487467c5384c1dcc DNK 2 sim card new 2023-09-19 6509ff93487467c5384c1dcc DNK 2 new sim card 2023-09-19 650abe22897d9b3838ffcc29 GBR 5 efficient polite great 2023-09-20 650abe22897d9b3838ffcc29 GBR 5 easy helping efficient 2023-09-20 650abe22897d9b3838ffcc29 GBR 5 polite great service 2023-09-20 650abe22897d9b3838ffcc29 GBR 5 helping efficient polite 2023-09-20 650abe22897d9b3838ffcc29 GBR 5 natasha quick easy 2023-09-20 650af5b8667a1c54a261a49d DEU 5 sonja quick help 2023-09-19 650af5b8667a1c54a261a49d DEU 5 thanks sonja quick 2023-09-19 650af5b8667a1c54a261a49d DEU 5 good customer service 2023-09-19 650af5b8667a1c54a261a49d DEU 5 customer service thanks 2023-09-19 650af5b8667a1c54a261a49d DEU 5 service thanks sonja 2023-09-19 650af616f07b267487e66aaf GBR 5 yesterday 19 23 2023-09-19 650af616f07b267487e66aaf GBR 5 online help iqbal 2023-09-19 650af616f07b267487e66aaf GBR 5 couple issues sim 2023-09-19 650af616f07b267487e66aaf GBR 5 sim plan contacted 2023-09-19 650af616f07b267487e66aaf GBR 5 issues sim plan 2023-09-19 650afe783eded0c035a65153 GBR 5 chat rushda khan 2023-09-20 650afe783eded0c035a65153 GBR 5 bought pay monthly 2023-09-20 650afe783eded0c035a65153 GBR 5 online chat rushda 2023-09-20 650afe783eded0c035a65153 GBR 5 monthly sim easy 2023-09-20 650afe783eded0c035a65153 GBR 5 pay monthly sim 2023-09-20 650b113ebe76149b8058fbdc GBR 5 problem record time 2023-09-20 650b113ebe76149b8058fbdc GBR 5 wonderful chat service 2023-09-20 650b113ebe76149b8058fbdc GBR 5 natasha gade sorted 2023-09-20 650b113ebe76149b8058fbdc GBR 5 service natasha gade 2023-09-20 650b113ebe76149b8058fbdc GBR 5 chat service natasha 2023-09-20 650b11abb33a358e54d71907 DEU 5 helpful concerns quickly 2023-09-20 650b11abb33a358e54d71907 DEU 5 experience nice helpful 2023-09-20 650b11abb33a358e54d71907 DEU 5 phone great experience 2023-09-20 650b11abb33a358e54d71907 DEU 5 mr idrissi phone 2023-09-20 650b11abb33a358e54d71907 DEU 5 idrissi phone great 2023-09-20 650c0213798aca410a142e1a GBR 4 wanted suspend service 2023-09-21 650c0213798aca410a142e1a GBR 4 john cancelled service 2023-09-21 650c0213798aca410a142e1a GBR 4 minutes rejoin lebara 2023-09-21 650c0213798aca410a142e1a GBR 4 lebara return uk 2023-09-21 650c0213798aca410a142e1a GBR 4 rejoin lebara return 2023-09-21 650c4351f08764f4b1cfd127 GBR 5 access emergency good 2023-09-21 650c4351f08764f4b1cfd127 GBR 5 affordable packages easy 2023-09-21 650c4351f08764f4b1cfd127 GBR 5 good demand customer 2023-09-21 6